In [1]:
# Your code here - remember to use markdown cells for comments as well!
import os

import pandas as pd
import numpy as np

from scipy import stats, linalg

from sklearn import linear_model
from sklearn import neighbors
from sklearn import preprocessing
from sklearn.metrics import mean_squared_error

from math import log

import matplotlib.pyplot as plt
%matplotlib inline

import seaborn as sns
# set style
sns.set_style('whitegrid')
# overriding font size and line width
# sns.set_context("notebook", font_scale=1.5, rc={"lines.linewidth": 2.5})

# map visualization
import folium

# don't print matching warnings
import warnings
warnings.filterwarnings('ignore') 



In [2]:
# read data and read date correctly
data = pd.read_csv("kc_house_data.csv", parse_dates = ['date'])

In [3]:
# Set zipcode type to string
data['zipcode'] = data['zipcode'].astype('str')

# Convert sqft_basement to int
data['sqft_basement'] = pd.to_numeric(data['sqft_basement'], errors='coerce')

# set category and order them
data['grade'] = data['grade'].astype('category', ordered = False)
data['waterfront'] = data['waterfront'].astype('category', ordered = True)
data['condition'] = data['condition'].astype('category', ordered = True)

# Drop columns which are not in the offical dataset (kaggle) and might mess up our stuff
# data.drop(columns=['sqft_living15', 'sqft_lot15'], inplace=True)

# sort data by date
data = data.sort_values(by = ['date'])

In [4]:
# get the mean value across all data points
zipcode_data = data.groupby('zipcode').aggregate(np.mean)
zipcode_data.reset_index(inplace = True)

# count number of entries grouped by zipcode
data['count'] = 1

temp_df = data.groupby('zipcode').sum()
temp_df.reset_index(inplace = True)
temp_df = temp_df[['zipcode', 'count']]

data.drop(['count'], axis = 1, inplace = True)

# merge the count values into the zipcode data
zipcode_data = pd.merge(zipcode_data, temp_df, how='left', on=['zipcode'])
zipcode_data.head(2)

zipcode            id          price  bedrooms  bathrooms  sqft_living  \
0   98001  4.651274e+09  281194.869806  3.393352   2.011773  1903.783934   
1   98002  4.850894e+09  234284.035176  3.326633   1.839196  1627.743719   

       sqft_lot    floors      view   sqft_above  sqft_basement     yr_built  \
0  14967.002770  1.430748  0.094708  1723.756233     184.107649  1980.867036   
1   7517.633166  1.334171  0.010050  1522.537688     105.737374  1967.773869   

   yr_renovated        lat        long  sqft_living15    sqft_lot15  count  
0     28.038732  47.309106 -122.270704    1830.099723  11218.875346    361  
1     60.212121  47.308780 -122.213357    1479.030151   7585.482412    199

In [5]:
geo_data = os.path.join('data', 'king_county_wa_zipcode_area.geojson')

In [6]:
def show_zipcode_map(col):
    m = folium.Map(location=[47.35, -121.9], zoom_start=9)

    m.choropleth(
        geo_data = geo_data,
        name = 'choropleth',
        data = zipcode_data,
        columns = ['zipcode', col], 
        key_on = 'feature.properties.ZIPCODE',
        fill_color = 'OrRd', 
        fill_opacity = 0.4,
        line_opacity = 0.2,
        legend_name = col
    )

    folium.LayerControl().add_to(m)
    m.save(col + '.html')
    
    return m
    
show_zipcode_map('count')

In [7]:
# style_function = lambda x: {'fillColor': '#0000ff' if data['properties']['name']=='Alabama' else '#00ff00'}
style_function = lambda x: {'fillColor': '#0000ff' if data['zipcode'] else '#00ff00'}
m = folium.Map(location=[47.35, -121.9], zoom_start=9)
folium.TopoJson(open(geo_data), 'feature.properties.ZIPCODE', style_function=style_function).add_to(m)
m

AttributeError: 'NoneType' object has no attribute 'get'